<a href="https://colab.research.google.com/github/dingjun6953/Pytorch_lightning_practice_codes/blob/main/best_template_minist_cifar10_lightning_v4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install pytorch_lightning pandas seaborn torch torchmetrics torchvision 


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 826.4/826.4 KB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 517.2/517.2 KB 30.1 MB/s eta 0:00:00


In [10]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import MNIST
from torchmetrics.classification import MultilabelAccuracy

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 256 if torch.cuda.is_available() else 64

class LitMNIST(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        #pytorch_lightning.utilities.seed.seed_everything(1234,workers=True)


        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (1, 28, 28)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [
                transforms.ToTensor(),
                transforms.Normalize((0.1307,), (0.3081,))
                #transforms.Normalize((0.5,), (0.5,))
            ]
        )
        #self.model=model
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v2
            nn.Conv2d(1, 32, kernel_size=3, padding=1),
            nn.ReLU(),
            #nn.MaxPool2d(2, 2),  # output: 64 x 14 x 14
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.ReLU(),
            nn.MaxPool2d(2, 2),  # output: 64 x 14 x 14

            nn.Conv2d(64, 256, kernel_size=3, stride=1, padding=1),
            nn.ReLU(),
            # nn.Conv2d(128, 128, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # #nn.MaxPool2d(2, 2),  # output: 128 x 7 x 7

            # nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # nn.Conv2d(256, 256, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            nn.MaxPool2d(2, 2),  # output: 256 x 7 x 7

            nn.Flatten(),
            nn.Linear(256 * 7 * 7, 512),
            nn.ReLU(),
            #nn.Linear(1024, 512),
            #nn.ReLU(),
            #nn.Dropout(inplace=True),
            nn.Linear(512, self.num_classes),

        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)

    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.nll_loss(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.nll_loss(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.nll_loss(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.model.parameters(), lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=1)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        MNIST(self.data_dir, train=True, download=True)
        MNIST(self.data_dir, train=False, download=True)

    def setup(self, stage=None):

        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            mnist_full = MNIST(self.data_dir, train=True, transform=self.transform)
            self.mnist_train, self.mnist_val = random_split(mnist_full, [55000, 5000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.mnist_test = MNIST(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        return DataLoader(self.mnist_train, batch_size=BATCH_SIZE)

    def val_dataloader(self):
        return DataLoader(self.mnist_val, batch_size=BATCH_SIZE)

    def test_dataloader(self):
        return DataLoader(self.mnist_test, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitMNIST()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)
trainer = Trainer(
    fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=1,
    auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=3,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")

INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.6 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.6 M     Trainable params
0         Non-trainable params
6.6 M     Total params
26.379    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=3` reached.
/usr/local/lib/python3.8/dist-packages/pytorch_lightning/trainer/connectors/checkpoint_connector.py:124: UserWarning: `.test(ckpt_path=None)` was called without a model. The best model of the previous `fit` call will be used. You can pass `.test(ckpt_path='best')` to use the best model or `.test(ckpt_path='last')` to use the last model. If you pass a value, this warning will be silenced.
  rank_zero_warn(
INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_3/checkpoints/epoch=2-step=645.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_3/checkpoints/epoch=2-step=645.ckpt



The time cost in training model: 0:00:54.374737



Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9925000071525574
        test_loss          0.020561087876558304
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        0.121711       NaN      NaN        NaN       NaN
0        0.094913       NaN      NaN        NaN       NaN
0        0.075353       NaN      NaN        NaN       NaN
0        0.075107       NaN      NaN        NaN       NaN
0             NaN  0.041752   0.9860        NaN       NaN
1        0.052547       NaN      NaN        NaN       NaN
1        0.021262       NaN      NaN        NaN       NaN
1        0.029856       NaN      NaN        NaN       NaN
1        0.004213       NaN      NaN        NaN       NaN
1             NaN  0.028607   0.9908        NaN       NaN
2        0.007216       NaN      NaN        NaN       NaN
2        0.050330       NaN      NaN        NaN       NaN
2        0.005009       NaN      NaN        NaN       NaN
2        0.010528       NaN      NaN        NaN       NaN
2             NaN  0.026682   0.9908        NaN       NaN
3             NaN       NaN      NaN   0.020561    0.9925

In [12]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


from torchvision.datasets.utils import download_url
import tarfile

# Dowload the dataset
dataset_url = "https://s3.amazonaws.com/fast-ai-imageclas/cifar10.tgz"
download_url(dataset_url, '.')

# Extract from archive
with tarfile.open('./cifar10.tgz', 'r:gz') as tar:
    tar.extractall(path='./data')
    
# Look into the data directory
data_dir = './data/cifar10'
print(os.listdir(data_dir))
classes = os.listdir(data_dir + "/train")
print(classes)


# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

# #define my more complex NN model
# class ResNet(nn.Module):
#   def __init__(self):
#     super().__init__()
#     self.l1=nn.Linear(28*28,64)
#     self.l2=nn.Linear(64,64)
#     self.l3=nn.Linear(64,10)
#     self.do=nn.Dropout(0.1)
#
#   def forward(self,x):
#     h1=nn.functional.relu(self.l1(x))
#     h2=nn.functional.relu(self.l2(h1))
#     do=self.do(h2+h1) # complete the residue step: output + input at this layer l2
#     logits =self.l3(do)
#     return logits
#
# mymodel=ResNet()



class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   #transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                #transforms.RandomHorizontalFlip(),
                transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
#Fully connected NN
            # nn.Flatten(),
            # nn.Linear(channels * width * height,64),
            # nn.ReLU(),
            # nn.Dropout(0.1),
            # nn.Linear(64, 64),
            # nn.ReLU(),
            # nn.Dropout(0.1),
            # nn.Linear(64, self.num_classes),
#CNN-v1
            # nn.Conv2d(1, 32, kernel_size=3, padding=1),
            # nn.ReLU(),
            # #nn.MaxPool2d(2, 2),  # output: 64 x 14 x 14
            # nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # nn.MaxPool2d(2, 2),  # output: 64 x 14 x 14

            # nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # nn.Conv2d(128, 128, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # #nn.MaxPool2d(2, 2),  # output: 128 x 7 x 7

            # nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # nn.Conv2d(256, 256, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # nn.MaxPool2d(2, 2),  # output: 128 x 7 x 7

            # nn.Flatten(),
            # nn.Linear(256 * 7 * 7, 1024),
            # nn.ReLU(),
            # nn.Linear(1024, 512),
            # nn.ReLU(),
            # #nn.Dropout(inplace=True),
            # nn.Linear(512, self.num_classes),

#CNN-v2
            # nn.Conv2d(3, 32, kernel_size=3, padding=1),
            # nn.ReLU(),
            # #nn.MaxPool2d(2, 2),  # output: 64 x 14 x 14
            # nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # nn.MaxPool2d(2, 2),  # output: 64 x 16 x 16

            # nn.Conv2d(64, 256, kernel_size=3, stride=1, padding=1),
            # nn.ReLU(),
            # # nn.Conv2d(128, 128, kernel_size=3, stride=1, padding=1),
            # # nn.ReLU(),
            # # #nn.MaxPool2d(2, 2),  # output: 128 x 7 x 7

            # # nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            # # nn.ReLU(),
            # # nn.Conv2d(256, 256, kernel_size=3, stride=1, padding=1),
            # # nn.ReLU(),
            # nn.MaxPool2d(2, 2),  # output: 256 x 8 x 8

            # nn.Flatten(),
            # nn.Linear(256 * 8 * 8, 512),
            # nn.ReLU(),
            # #nn.Linear(1024, 512),
            # #nn.ReLU(),
            # #nn.Dropout(0.2),
            # nn.Linear(512, self.num_classes),

#CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 1024 x 1 x 1

            nn.Flatten(), 
#             nn.Linear(256*2*2, 1024),
#             nn.ReLU(),
#             nn.Linear(1024, 512),
#             nn.ReLU(),
            #nn.Dropout(inplace=True),
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),



#RNN does not work well here

          # #nn.LSTM(128,256),
          # #nn.Dropout(0.2),
          # nn.LSTM(256,128),
          # #nn.Dropout(0.2),
          # nn.Linear(128,32),
          # nn.Linear(32,self.num_classes),

        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)

    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        #loss = F.nll_loss(logits, y)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        #loss = F.nll_loss(logits, y)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        #loss = F.nll_loss(logits, y)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        #optimizer = opt_func(model.parameters(), 0.01, weight_decay=weight_decay)
        # Set up one-cycle learning rate scheduler
        #lr_scheduler = torch.optim.lr_scheduler.OneCycleLR(optimizer, 0.01, steps_per_epoch=None)
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
#         optimizer = torch.optim.Adam(self.model.parameters(), lr=1e-3)
#         lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=1)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):

        # Assign train/val datasets for use in dataloaders
#         if stage == "fit" or stage is None:
#             datasets = CIFAR10(self.data_dir, train=True, transform=self.transform)
#             self.train_data, self.val_data = random_split(datasets, [45000, 5000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        # PyTorch datasets
        data_dir = './data/cifar10'
        stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
        train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         # tt.RandomRotate
                         # tt.RandomResizedCrop(256, scale=(0.5,0.9), ratio=(1, 1)), 
                         # tt.ColorJitter(brightness=0.1, contrast=0.1, saturation=0.1, hue=0.1),
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])

        train_ds = ImageFolder(data_dir+'/train', train_tfms)
        train_dl = DataLoader(train_ds, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
#         print("training size:")
#         print(len(train_dl)
        return train_dl

    def val_dataloader(self):
        data_dir = './data/cifar10'
        stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
        valid_tfms = transforms.Compose([transforms.ToTensor(), transforms.Normalize(*stats)])
        valid_ds = ImageFolder(data_dir+'/test', valid_tfms)
        valid_dl = DataLoader(valid_ds, BATCH_SIZE, num_workers=2, pin_memory=True)
#         print("validation size:")
#         print(len(valid_dl))
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.1,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=10,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


Using downloaded and verified file: ./cifar10.tgz
['train', 'test']
['bird', 'airplane', 'ship', 'horse', 'truck', 'dog', 'cat', 'automobile', 'frog', 'deer']


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


  0%|          | 0/170498071 [00:00<?, ?it/s]

Extracting ./cifar-10-python.tar.gz to .
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


...


The time cost in training model: 0:06:46.547449

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_4/checkpoints/epoch=9-step=2500.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_4/checkpoints/epoch=9-step=2500.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.7990999817848206
        test_loss           0.6041390895843506
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.422009       NaN      NaN        NaN       NaN
0        1.208097       NaN      NaN        NaN       NaN
0        1.272878       NaN      NaN        NaN       NaN
0        1.381376       NaN      NaN        NaN       NaN
0        0.973507       NaN      NaN        NaN       NaN
...           ...       ...      ...        ...       ...
9        0.508519       NaN      NaN        NaN       NaN
9        0.510411       NaN      NaN        NaN       NaN
9        0.416660       NaN      NaN        NaN       NaN
9             NaN  0.604139   0.7991        NaN       NaN
10            NaN       NaN      NaN   0.604139    0.7991

[61 rows x 5 columns]

In [13]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [45000, 5000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.1,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_5/checkpoints/epoch=49-step=11250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_5/checkpoints/epoch=49-step=11250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9043999910354614
        test_loss           0.2946362793445587
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.624992       NaN      NaN        NaN       NaN
0        1.233482       NaN      NaN        NaN       NaN
0        1.152766       NaN      NaN        NaN       NaN
0        1.230930       NaN      NaN        NaN       NaN
0             NaN  1.544574   0.5088        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.076621       NaN      NaN        NaN       NaN
49       0.101841       NaN      NaN        NaN       NaN
49       0.133585       NaN      NaN        NaN       NaN
49            NaN  0.325514   0.8930        NaN       NaN
50            NaN       NaN      NaN   0.294636    0.9044

[276 rows x 5 columns]

In [14]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10), #fully connected network
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        datasets = CIFAR10(self.data_dir, train=True, transform=self.transform) # image augumention 
        self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.1,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...


The time cost in training model: 0:12:21.084843

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_6/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_6/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc             0.859000027179718
        test_loss           0.5839084982872009
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.485909       NaN      NaN        NaN       NaN
0        1.242673       NaN      NaN        NaN       NaN
0        1.078139       NaN      NaN        NaN       NaN
0        0.975766       NaN      NaN        NaN       NaN
0             NaN  1.037380    0.638        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.000168       NaN      NaN        NaN       NaN
49       0.000202       NaN      NaN        NaN       NaN
49       0.000220       NaN      NaN        NaN       NaN
49            NaN  0.667791    0.849        NaN       NaN
50            NaN       NaN      NaN   0.583908     0.859

[296 rows x 5 columns]

In [15]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.1,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_7/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_7/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9054999947547913
        test_loss           0.2963451147079468
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.588050       NaN      NaN        NaN       NaN
0        1.289134       NaN      NaN        NaN       NaN
0        1.398263       NaN      NaN        NaN       NaN
0        1.130882       NaN      NaN        NaN       NaN
0             NaN  1.255120    0.556        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.163452       NaN      NaN        NaN       NaN
49       0.055960       NaN      NaN        NaN       NaN
49       0.097670       NaN      NaN        NaN       NaN
49            NaN  0.279066    0.910        NaN       NaN
50            NaN       NaN      NaN   0.296345    0.9055

[296 rows x 5 columns]

In [16]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.2,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_8/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_8/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9053000211715698
        test_loss           0.2997382581233978
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.586016       NaN      NaN        NaN       NaN
0        1.228223       NaN      NaN        NaN       NaN
0        1.198850       NaN      NaN        NaN       NaN
0        1.201092       NaN      NaN        NaN       NaN
0             NaN  1.103874    0.603        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.101299       NaN      NaN        NaN       NaN
49       0.093860       NaN      NaN        NaN       NaN
49       0.102936       NaN      NaN        NaN       NaN
49            NaN  0.361645    0.878        NaN       NaN
50            NaN       NaN      NaN   0.299738    0.9053

[296 rows x 5 columns]

In [17]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.3,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_9/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_9/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9088000059127808
        test_loss           0.3083900809288025
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.573018       NaN      NaN        NaN       NaN
0        1.371304       NaN      NaN        NaN       NaN
0        1.179565       NaN      NaN        NaN       NaN
0        1.006000       NaN      NaN        NaN       NaN
0             NaN  1.207013    0.565        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.078496       NaN      NaN        NaN       NaN
49       0.059339       NaN      NaN        NaN       NaN
49       0.044536       NaN      NaN        NaN       NaN
49            NaN  0.297656    0.906        NaN       NaN
50            NaN       NaN      NaN    0.30839    0.9088

[296 rows x 5 columns]

In [18]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.4,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_10/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_10/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9067000150680542
        test_loss           0.29666954278945923
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.536058       NaN      NaN        NaN       NaN
0        1.514817       NaN      NaN        NaN       NaN
0        1.261545       NaN      NaN        NaN       NaN
0        1.053881       NaN      NaN        NaN       NaN
0             NaN  1.178616    0.589        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.070311       NaN      NaN        NaN       NaN
49       0.105177       NaN      NaN        NaN       NaN
49       0.046802       NaN      NaN        NaN       NaN
49            NaN  0.305150    0.904        NaN       NaN
50            NaN       NaN      NaN    0.29667    0.9067

[296 rows x 5 columns]

In [19]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.4,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_11/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_11/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9121999740600586
        test_loss           0.2995203733444214
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.494907       NaN      NaN        NaN       NaN
0        1.476132       NaN      NaN        NaN       NaN
0        1.197288       NaN      NaN        NaN       NaN
0        1.203643       NaN      NaN        NaN       NaN
0             NaN  1.132360    0.591        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.095166       NaN      NaN        NaN       NaN
49       0.075614       NaN      NaN        NaN       NaN
49       0.104902       NaN      NaN        NaN       NaN
49            NaN  0.309573    0.915        NaN       NaN
50            NaN       NaN      NaN    0.29952    0.9122

[296 rows x 5 columns]

In [20]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.5,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_12/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_12/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc             0.90829998254776
        test_loss           0.30924737453460693
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.552546       NaN      NaN        NaN       NaN
0        1.326427       NaN      NaN        NaN       NaN
0        1.126845       NaN      NaN        NaN       NaN
0        0.968951       NaN      NaN        NaN       NaN
0             NaN  1.293926    0.562        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.038682       NaN      NaN        NaN       NaN
49       0.062686       NaN      NaN        NaN       NaN
49       0.066213       NaN      NaN        NaN       NaN
49            NaN  0.338122    0.898        NaN       NaN
50            NaN       NaN      NaN   0.309247    0.9083

[296 rows x 5 columns]

In [21]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            #CNN-v3
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.4, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.5,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_13/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_13/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9071999788284302
        test_loss           0.31268832087516785
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.439363       NaN      NaN        NaN       NaN
0        1.338584       NaN      NaN        NaN       NaN
0        1.316596       NaN      NaN        NaN       NaN
0        1.176085       NaN      NaN        NaN       NaN
0             NaN  1.099409    0.604        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.088283       NaN      NaN        NaN       NaN
49       0.092533       NaN      NaN        NaN       NaN
49       0.090834       NaN      NaN        NaN       NaN
49            NaN  0.311090    0.897        NaN       NaN
50            NaN       NaN      NaN   0.312688    0.9072

[296 rows x 5 columns]

In [22]:
import os
from datetime import datetime
import pandas as pd
import seaborn as sn
import torch
import pytorch_lightning
from IPython.core.display import display
from pytorch_lightning import LightningModule, Trainer
from pytorch_lightning.callbacks.progress import TQDMProgressBar
from pytorch_lightning.loggers import CSVLogger 
from pytorch_lightning.loggers import TensorBoardLogger
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader, random_split
from torchmetrics import Accuracy
from torchvision import transforms
from torchvision.datasets import CIFAR10
from torchvision.datasets import ImageFolder


#from torchvision.datasets.utils import download_url
#import tarfile

# set the current directory as working directory
PATH_DATASETS = os.environ.get("PATH_DATASETS", ".")
# setting of batch size
BATCH_SIZE = 200 if torch.cuda.is_available() else 64

class LitCIFAR10(LightningModule):
    def __init__(self, data_dir=PATH_DATASETS):
        super().__init__()
        # Set our init args as class attributes
        self.data_dir = data_dir
        
        # Hardcode some dataset specific attributes
        self.num_classes = 10
        self.dims = (3, 32, 32)
        channels, width, height = self.dims
        self.transform = transforms.Compose(
            [   transforms.ToTensor(),
                transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            ]
        )
        
        # Define PyTorch model
        self.model = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 64 x 16 x 16

            nn.Conv2d(64, 128, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 128 x 8 x 8
            nn.Conv2d(128, 256, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(256),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output: 256 x 4 x 4

            nn.Conv2d(256, 512, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(512),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:512 x 2 x 2
            nn.Conv2d(512, 1024, kernel_size=3, stride=1, padding=1),
            nn.BatchNorm2d(1024),
            nn.ReLU(),
            nn.MaxPool2d(2, 2), # output:1024 x 1 x 1

            nn.Flatten(), 
            nn.Dropout(p=0.2, inplace=False),
            nn.Linear(1024, 10),
        )
        self.train_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.val_accuracy = Accuracy(task="multiclass", num_classes=10)
        self.test_accuracy = Accuracy(task="multiclass", num_classes=10)


    def forward(self, x):
        x = self.model(x)
        return F.log_softmax(x, dim=1)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y) # Calculate loss
        preds = torch.argmax(logits, dim=1)
        self.train_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("train_loss", loss, prog_bar=True)
        self.log("train_acc", self.train_accuracy, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.val_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", self.val_accuracy, prog_bar=True)

    def test_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        preds = torch.argmax(logits, dim=1)
        self.test_accuracy.update(preds, y)

        # Calling self.log will surface up scalars for you in TensorBoard
        self.log("test_loss", loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy, prog_bar=True)

    def configure_optimizers(self):
         # Set up cutom optimizer with weight decay
        optimizer = torch.optim.Adam(self.model.parameters(),weight_decay=1e-4,lr=1e-3)
        lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15)
        return [optimizer], [lr_scheduler]

    def validation_epoch_end(self, outputs):

        return 
    ####################
    # DATA RELATED HOOKS
    ####################

    def prepare_data(self):
        # download
        CIFAR10(self.data_dir, train=True, download=True)
        CIFAR10(self.data_dir, train=False, download=True)

    def setup(self, stage=None):
        # Assign train/val datasets for use in dataloaders
        if stage == "fit" or stage is None:
            stats = ((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
            train_tfms =transforms.Compose([transforms.RandomCrop(32, padding=4, padding_mode='reflect'), 
                         transforms.RandomHorizontalFlip(), 
                         transforms.ToTensor(), 
                         transforms.Normalize(*stats,inplace=True)])
            datasets = CIFAR10(self.data_dir, train=True, transform=train_tfms) # image augumention 
            self.train_data, self.val_data = random_split(datasets, [49000, 1000])

        # Assign test dataset for use in dataloader(s)
        if stage == "test" or stage is None:
            self.test_data = CIFAR10(self.data_dir, train=False, transform=self.transform)

    def train_dataloader(self):
        train_dl = DataLoader(self.train_data, BATCH_SIZE, shuffle=True, num_workers=2, pin_memory=True)
        return train_dl

    def val_dataloader(self):
        valid_dl = DataLoader(self.val_data, BATCH_SIZE, num_workers=2, pin_memory=True)
        return valid_dl

    def test_dataloader(self):
        return DataLoader(self.test_data, batch_size=BATCH_SIZE)


start=datetime.now()
model = LitCIFAR10()


#logger = TensorBoardLogger("tb_logs", name="my_model")
#logger = TensorBoardLogger("lightning_logs", name=None)

trainer = Trainer(
    precision=16,
    #fast_dev_run=False,
    #deterministic=True,
    gradient_clip_val=0.5,
    #auto_lr_find=True,
    accelerator="auto",
    devices=1 if torch.cuda.is_available() else None,  # limiting got iPython runs
    max_epochs=50,
    callbacks=[TQDMProgressBar(refresh_rate=20)],
    #logger=logger,
    logger=CSVLogger(save_dir="logs/"),
)
trainer.fit(model)
print()
print(f"The time cost in training model: {datetime.now()-start}")
print()
trainer.test()
metrics = pd.read_csv(f"{trainer.logger.log_dir}/metrics.csv")
del metrics["step"]
metrics.set_index("epoch", inplace=True)
display(metrics.dropna(axis=1, how="all"))
#sn.relplot(data=metrics, kind="line")


INFO:pytorch_lightning.utilities.rank_zero:Using 16bit None Automatic Mixed Precision (AMP)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type               | Params
------------------------------------------------------
0 | model          | Sequential         | 6.3 M 
1 | train_accuracy | MulticlassAccuracy | 0     
2 | val_accuracy   | MulticlassAccuracy | 0     
3 | test_accuracy  | MulticlassAccuracy | 0     
------------------------------------------------------
6.3 M     Trainable params
0         Non-trainable params
6.3 M     Total params
12.605    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

...

Files already downloaded and verified
Files already downloaded and verified


INFO:pytorch_lightning.utilities.rank_zero:Restoring states from the checkpoint path at logs/lightning_logs/version_14/checkpoints/epoch=49-step=12250.ckpt
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.utilities.rank_zero:Loaded model weights from checkpoint at logs/lightning_logs/version_14/checkpoints/epoch=49-step=12250.ckpt


Testing: 0it [00:00, ?it/s]

────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        test_acc            0.9146000146865845
        test_loss            0.302154541015625
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────


train_loss  val_loss  val_acc  test_loss  test_acc
epoch                                                    
0        1.459013       NaN      NaN        NaN       NaN
0        1.335079       NaN      NaN        NaN       NaN
0        1.288901       NaN      NaN        NaN       NaN
0        1.020427       NaN      NaN        NaN       NaN
0             NaN  1.446694    0.491        NaN       NaN
...           ...       ...      ...        ...       ...
49       0.050048       NaN      NaN        NaN       NaN
49       0.037918       NaN      NaN        NaN       NaN
49       0.060758       NaN      NaN        NaN       NaN
49            NaN  0.378019    0.893        NaN       NaN
50            NaN       NaN      NaN   0.302155    0.9146

[296 rows x 5 columns]